# .dat to .csv
The purpose of this tool is to convert _.dat_ files into _.csv_ files where each row is a sample to be analyzed.

The .dat files are obtained by running the *cap2dat* program on _.pcap_ files.

Firstly the data is loaded to a numpy array.

In [1]:
import os
import numpy as np
from collections import defaultdict, deque
from scalogram import *
import pandas as pd
from sklearn.externals import joblib 
import re

base_url = '../../../shared/'
sampling_interval = '1s' # 1s or 01s
sample_size = 60 # number of intervals for each sample
all_data = np.zeros(5)

def split_number(s):
    return list(filter(None, re.split(r'(\d+)', s)))

for path, subdirs, files in os.walk(base_url):
    for name in files:
        if os.path.basename(path) != sampling_interval:
            continue
        
        print(os.path.join(path, name))
        
        #[up_n_packets, up_n_bytes, up_flag, down_n_packets, down_n_bytes, down_flag]
        data = np.loadtxt(os.path.join(path, name))
        data = np.delete(data, [2,5], 1)
        label = np.full((np.size(data, 0), 1), split_number(name.split('.')[0])[0])
        data = np.hstack((data, label))
        all_data = np.vstack((all_data, data))

../../../shared/openvpn/netflix/dat/1s/netflix-openvpn.pcapng_1.00s.dat
../../../shared/openvpn/youtube/dat/1s/youtube-openvpn.pcapng_1.00s.dat
../../../shared/openvpn/acestream/dat/1s/acestream-openvpn.pcapng_1.00s.dat
../../../shared/openvpn/browsing/dat/1s/browsing-openvpn.pcapng_1.00s.dat
../../../shared/openvpn/twitch/dat/1s/twitch-openvpn.pcapng_1.00s.dat
../../../shared/normal/netflix/dat/1s/netflix2.pcapng_1.00s.dat
../../../shared/normal/netflix/dat/1s/netflix4.pcapng_1.00s.dat
../../../shared/normal/netflix/dat/1s/netflix3.pcapng_1.00s.dat
../../../shared/normal/youtube/dat/1s/youtube1.pcapng_1.00s.dat
../../../shared/normal/youtube/dat/1s/youtube4.pcapng_1.00s.dat
../../../shared/normal/youtube/dat/1s/youtube3.pcapng_1.00s.dat
../../../shared/normal/youtube/dat/1s/youtube2.pcapng_1.00s.dat
../../../shared/normal/youtube/dat/1s/youtube51.pcapng_1.00s.dat
../../../shared/normal/youtube/dat/1s/youtube53.pcapng_1.00s.dat
../../../shared/normal/youtube/dat/1s/youtube52.pcapng_1.0

# Normalize

Apply a standard scaler to all of the data and save it (we will need it for live classification).

In [2]:
from sklearn.preprocessing import StandardScaler

to_scale = all_data[:, :-1]
scaler = StandardScaler()
scaled = scaler.fit_transform(np.asarray(to_scale))
scaled = np.hstack((scaled.astype(float), np.matrix(all_data[:, -1]).T))
joblib.dump(scaler, '../models/std_scaler_' + sampling_interval + '_' + str(sample_size) + '.sav')


/home/agro/work/thesis/env/lib/python3.6/site-packages/sklearn/utils/validation.py:475: DataConversionWarning: Data with input dtype <U32 was converted to float64 by StandardScaler.
  warnings.warn(msg, DataConversionWarning)


['../models/std_scaler_1s_60.sav']

Save row with zeros so we can count the 'silences' later on.

In [3]:
zeros = scaled[0].tolist()[0][:-1]
zeros = [float(i) for i in zeros]
zeros

[-0.30389649822236503,
 -0.17693322554268284,
 -0.40600874547266963,
 -0.4304917544891338]

# Divide data into buckets

In [4]:
def get_info(data):
    info = []
    up = defaultdict(list)
    down = defaultdict(list)
    result = {}
    count = 0
    current_label = data[1, 4]
    for interval_unit in data[1:]:
        if current_label != interval_unit.item(4):
            current_label = interval_unit.item(4)
        up['packet_count'].append(float(interval_unit.item(0)))
        up['byte_count'].append(float(interval_unit.item(1)))
        down['packet_count'].append(float(interval_unit.item(2)))
        down['byte_count'].append(float(interval_unit.item(3)))
        count+=1
        if count >= sample_size:
            result['up'] = up
            result['down'] = down
            info.append((result, current_label))
            up = defaultdict(list)
            down = defaultdict(list)
            result = {}
            count = 0
    return info
info = get_info(scaled)

# Scalogram scales

In [5]:
#Scalogram
N = sample_size
dj=1/32
s0=2
J=1/dj * np.log2(0.5*N/s0)
scales=s0*2**(np.arange(J)*dj)

Get scalogram data

In [6]:
from scipy.signal import argrelextrema

def calc_scalogram(data, scales):
    S,scales= scalogramCWT(data,scales)
    return S
def show_scalo(data, scales, colors):
    for i in range (0, len(data)):
        plt.plot(scales, data[i], colors[i], lw=3)
    plt.show()
    
# Get top X spikes from scalogram, sorted by value
def get_spikes(scalo, comparator):
    len(scalo)
    spikes = deque([(-1,-1)] * 5, maxlen=5)
    #aux = argrelextrema(scalo, comparator, order=int(len(scalo)/10))
    aux = argrelextrema(scalo, comparator)
    if aux[0].size:
        for x in np.nditer(aux) or []:
            spikes.append((scalo[x], scales[x]))
    ordered = sorted(spikes, key=lambda x: x[1], reverse=True)
    values = np.hstack(zip(*ordered))
    return values

scalos_up = []
scalos_down = []
for sample in info:
    print(sample)
    scalos_up.append(
        (
            (calc_scalogram((sample[0]['up']['byte_count']), scales), 
             calc_scalogram(np.asarray(sample[0]['up']['packet_count']), scales)
            ),
             sample[1]
        )
    )
    scalos_down.append(
        (    
            (calc_scalogram(np.asarray(sample[0]['down']['byte_count']), scales),
             calc_scalogram(np.asarray(sample[0]['down']['packet_count']), scales)
            ),
            sample[1]
        )
    )

({'up': defaultdict(<class 'list'>, {'packet_count': [0.43723904118157086, 1.0094646204422841, 2.7709542047930342, 3.675828991274584, 3.520707599306318, 3.505195460109492, 1.059448180076503, -0.3021729272004954, -0.30389649822236503, -0.30389649822236503, -0.2384007993913195, 0.5061818820563556, -0.2659779357412334, -0.28666078800366884, -0.2504657965444068, -0.28838435902553844, -0.3021729272004954, -0.10051511764175004, 0.6733682711777086, 3.5930975822248423, -0.3021729272004954, 0.8508960864302793, 3.6999589855807584, 2.733035642311903, 3.698235414558889, 3.594821153246712, 3.5155368862407093, 3.2914726533976593, 0.9112210721957159, -0.2935550720911473, -0.30389649822236503, -0.3021729272004954, -0.30389649822236503, -0.29527864311301694, -0.30389649822236503, -0.30389649822236503, -0.30389649822236503, 0.16319124870430157, -0.29527864311301694, -0.2918315010692777, -0.3021729272004954, 0.17180910381364967, -0.30389649822236503, -0.2901079300474081, -0.24874222552253722, 0.413109046

({'up': defaultdict(<class 'list'>, {'packet_count': [-0.2987257851567562, -0.036742989832574166, -0.3004493561786258, -0.30389649822236503, -0.30389649822236503, 0.37001977132865577, -0.30389649822236503, -0.30389649822236503, -0.30389649822236503, 0.1201019731575611, -0.30389649822236503, -0.30389649822236503, -0.30389649822236503, 0.22006909242599898, -0.2987257851567562, -0.30389649822236503, -0.28838435902553844, 0.14595553848560539, -0.3021729272004954, -0.30389649822236503, -0.21944151815075372, 0.34588977702248114, -0.2901079300474081, -0.2935550720911473, -0.2935550720911473, 0.07356555556708141, -0.30389649822236503, -0.28149007493806, -0.2901079300474081, 0.13216697031064845, -0.30389649822236503, -0.30389649822236503, -0.30389649822236503, 0.08907769476390798, -0.29700221413488653, -0.30389649822236503, -0.30389649822236503, 0.32003621169443686, -0.3021729272004954, -0.30389649822236503, -0.2987257851567562, 0.12182554417943073, -0.3021729272004954, -0.30389649822236503, -0

({'up': defaultdict(<class 'list'>, {'packet_count': [-0.30389649822236503, 0.2700526520602179, -0.30389649822236503, -0.30389649822236503, -0.3004493561786258, 0.2114512373166509, -0.3004493561786258, -0.29700221413488653, -0.3021729272004954, 0.11148411804821302, -0.30389649822236503, -0.30389649822236503, -0.29700221413488653, 0.30280050147574067, -0.30389649822236503, -0.30389649822236503, -0.3021729272004954, 0.147679109507475, -0.3021729272004954, -0.30389649822236503, -0.30389649822236503, 0.07528912658895102, -0.3004493561786258, -0.28149007493806, -0.30389649822236503, 0.05460627432651561, -0.30389649822236503, -0.2504657965444068, -0.2935550720911473, 0.2752233651258268, -0.2987257851567562, -0.30389649822236503, -0.30389649822236503, 0.04254127717342828, -0.3021729272004954, -0.30389649822236503, -0.30389649822236503, 0.05288270330464599, -0.30389649822236503, -0.30389649822236503, -0.30389649822236503, 0.06839484250147256, -0.30389649822236503, -0.30389649822236503, -0.3038

({'up': defaultdict(<class 'list'>, {'packet_count': [-0.30389649822236503, 0.2304105185572167, -0.3021729272004954, -0.3021729272004954, -0.3021729272004954, 0.41483261789726583, -0.30389649822236503, -0.30389649822236503, -0.2832136459599296, 0.08735412374203835, -0.30389649822236503, -0.3021729272004954, -0.30389649822236503, 0.006346285714166296, -0.30389649822236503, -0.30389649822236503, -0.3021729272004954, 0.009793427757905532, -0.30389649822236503, -0.30389649822236503, -0.30389649822236503, 0.25626408388526095, -0.28666078800366884, -0.27114864880684225, -0.30389649822236503, 0.039094135129689046, -0.3004493561786258, -0.30389649822236503, -0.30389649822236503, 0.08218341067642951, -0.30389649822236503, -0.30389649822236503, -0.30389649822236503, 0.07528912658895102, -0.30389649822236503, -0.30389649822236503, -0.30389649822236503, 0.32175978271630645, -0.30389649822236503, -0.30389649822236503, -0.3021729272004954, 0.08045983965455988, -0.30389649822236503, -0.30389649822236

({'up': defaultdict(<class 'list'>, {'packet_count': [-0.30389649822236503, -0.10913297275109814, -0.30389649822236503, -0.30389649822236503, -0.30389649822236503, 0.09941912089512568, -0.30389649822236503, -0.30389649822236503, -0.30389649822236503, 0.12182554417943073, -0.30389649822236503, -0.30389649822236503, -0.3021729272004954, 0.2217926634478686, -0.3021729272004954, -0.3021729272004954, -0.30389649822236503, -0.06432012618248806, -0.30389649822236503, -0.30389649822236503, -0.30389649822236503, -0.03846656085444378, -0.29700221413488653, -0.27976650391619035, -0.30389649822236503, 0.045988419217167516, -0.2901079300474081, -0.2366772283694499, -0.29700221413488653, 0.30280050147574067, -0.3004493561786258, -0.30389649822236503, -0.30389649822236503, 0.2597112259290002, -0.30389649822236503, -0.30389649822236503, -0.30389649822236503, 0.15974410666056232, -0.30389649822236503, -0.30389649822236503, -0.30389649822236503, 0.07873626863269027, -0.29700221413488653, -0.298725785156

...

({'up': defaultdict(<class 'list'>, {'packet_count': [0.07011841352334218, -0.07983226537931462, -0.1625636744290563, 0.20800409527291164, -0.16773438749466515, 0.19938624016356354, -0.2832136459599296, -0.2918315010692777, 0.1183784021356915, -0.1160272568385766, 0.12699625724503957, -0.3004493561786258, -0.29700221413488653, 0.1183784021356915, -0.15049867727596897, -0.07466155231370576, -0.028125134723226072, -0.3004493561786258, 0.13906125439812692, -0.17462867158214362, 0.11320768907008263, -0.2573600806318853, -0.30389649822236503, -0.3021729272004954, -0.3004493561786258, -0.02984870574509569, -0.17290510056027403, -0.3004493561786258, -0.2177179471288841, 0.12354911520130035, -0.29527864311301694, 0.17180910381364967, -0.3004493561786258, -0.3004493561786258, -0.3004493561786258, -0.2556365096100157, 0.07528912658895102, -0.2832136459599296, -0.2987257851567562, 0.07356555556708141, -0.0401901318763134, 0.1097605470263434, -0.30389649822236503, -0.29700221413488653, -0.29355507

({'up': defaultdict(<class 'list'>, {'packet_count': [-0.30389649822236503, -0.2918315010692777, 0.14078482541999654, -0.29700221413488653, -0.30389649822236503, -0.267701506763103, 0.021858424910992862, -0.2573600806318853, 0.008069856736035915, -0.2918315010692777, -0.2004822369101879, 0.05460627432651561, -0.14877510625409937, 0.018411282867253624, -0.3021729272004954, -0.209100092019536, 0.12182554417943073, -0.22978294428197144, 0.06494770045773332, -0.2918315010692777, -0.29527864311301694, 0.025305566954732097, -0.2763193618724511, 0.12699625724503957, -0.30389649822236503, -0.18152295566962212, 0.06839484250147256, -0.08845012048866271, -0.15566939034157784, -0.2935550720911473, -0.016060137570138744, -0.15739296136344746, -0.30389649822236503, 0.18732124301047623, -0.3021729272004954, 0.13389054133251804, -0.3004493561786258, -0.267701506763103, 0.11148411804821302, -0.27976650391619035, 0.23902837366656476, -0.2935550720911473, -0.30389649822236503, 0.11148411804821302, -0.30

({'up': defaultdict(<class 'list'>, {'packet_count': [-0.2987257851567562, -0.30389649822236503, 0.0442648481952979, -0.30389649822236503, 0.09597197885138645, -0.30389649822236503, -0.29700221413488653, 0.011516998779775151, -0.29700221413488653, -0.29527864311301694, -0.016060137570138744, -0.2987257851567562, 0.13561411235438767, -0.3021729272004954, -0.28149007493806, 0.15284982257308385, -0.29527864311301694, 0.09769554987325607, -0.29700221413488653, -0.2849372169817992, 0.11320768907008263, -0.3021729272004954, 0.13906125439812692, -0.29700221413488653, -0.012612995526399506, -0.18669366873523097, 0.13216697031064845, -0.2987257851567562, -0.2935550720911473, 0.1183784021356915, -0.2987257851567562, 0.11493126009195226, -0.29527864311301694, -0.30389649822236503, -0.2384007993913195, -0.059149413116879206, -0.19531152384457906, 0.006346285714166296, -0.27976650391619035, -0.29527864311301694, 0.14940268052934463, -0.10740940172922851, -0.08327940742305386, -0.3004493561786258, -

({'up': defaultdict(<class 'list'>, {'packet_count': [-0.15566939034157784, 0.008069856736035915, -0.055702271073139964, 0.025305566954732097, -0.2935550720911473, -0.16945795851653478, 0.028752708998471335, -0.1436043931884905, -0.01778370859200836, -0.30389649822236503, -0.2918315010692777, -0.30389649822236503, 0.20800409527291164, -0.17462867158214362, 0.0046227146922966774, -0.24184794143505875, -0.2901079300474081, -0.19703509486644868, -0.036742989832574166, -0.21082366304140562, -0.05397870005127035, -0.3021729272004954, -0.2504657965444068, 0.008069856736035915, -0.29700221413488653, 0.07528912658895102, -0.2987257851567562, 0.018411282867253624, -0.2918315010692777, -0.28666078800366884, 0.0046227146922966774, -0.14015725114475128, -0.08327940742305386, -0.30389649822236503, 0.014964140823514388, -0.30389649822236503, 0.04254127717342828, -0.30389649822236503, -0.1918643818008398, 0.025305566954732097, -0.22978294428197144, 0.09597197885138645, -0.2901079300474081, 0.07184198

({'up': defaultdict(<class 'list'>, {'packet_count': [0.021858424910992862, -0.1797993846477525, -0.29700221413488653, 0.061500558413994086, -0.16773438749466515, 0.10631340498260416, -0.26080722267562456, -0.30389649822236503, -0.29700221413488653, -0.1056858307073589, -0.033295847788834924, -0.30389649822236503, 0.025305566954732097, -0.14532796421036012, 0.03219985104221057, -0.07293798129183615, -0.29527864311301694, 0.11148411804821302, -0.29700221413488653, -0.16601081647279553, 0.1373376833762573, -0.0401901318763134, -0.12981582501353356, -0.30389649822236503, -0.09879154661988042, -0.08672654946679309, -0.07638512333557539, -0.07810869435744501, -0.29700221413488653, 0.18042695892299776, -0.2918315010692777, 0.10803697600447378, -0.29700221413488653, -0.30389649822236503, 0.1562969646168231, -0.30389649822236503, 0.16319124870430157, -0.2901079300474081, -0.21944151815075372, -0.00916585348266027, -0.2366772283694499, -0.005718711438921033, -0.29700221413488653, 0.040817706151

In [7]:
local_max_up_bytes = []
local_min_up_bytes = []
local_max_up_packet = []
local_min_up_packet = []
local_max_down_bytes = []
local_min_down_bytes = []
local_max_down_packet = []
local_min_down_packet = []

for scalo in scalos_up:
    local_max_up_bytes.append((get_spikes(scalo[0][0], np.greater), scalo[1]))
    local_min_up_bytes.append((get_spikes(scalo[0][0], np.less), scalo[1]))
    local_max_up_packet.append((get_spikes(scalo[0][1], np.greater), scalo[1]))
    local_min_up_packet.append((get_spikes(scalo[0][1], np.less), scalo[1]))

for scalo in scalos_down:
    local_max_down_bytes.append((get_spikes(scalo[0][0], np.greater), scalo[1]))
    local_min_down_bytes.append((get_spikes(scalo[0][0], np.less), scalo[1]))
    local_max_down_packet.append((get_spikes(scalo[0][1], np.greater), scalo[1]))
    local_min_down_packet.append((get_spikes(scalo[0][1], np.less), scalo[1]))

Get stats from the buckets

In [8]:
from itertools import groupby
from scipy import stats

def get_stats_numpy(data, zero):
    mean = np.mean(data)
    median = np.median(data)
    std = np.std(data)
    var = np.var(data)
    skew = stats.skew(data)
    kurt = stats.kurtosis(data)
    pc = [25,50,75,90]
    percentiles = np.array(np.percentile(data, pc))
    silences = np.count_nonzero(np.asarray(data)==zero)
    silence_mean = np.mean(list(sum(1 for _ in g) for k, g in groupby(data) if k==zero ))
    longest_silence = max(sum(1 for _ in g) for k, g in groupby(data) if k==zero) if silences > 0 else 0
    shortest_silence = min(sum(1 for _ in g) for k, g in groupby(data) if k==zero) if silences > 0 else 0
    
    #print("Mean: " + str(mean))
    #print("Media: " + str(median))
    #print("StdDev: " + str(std))
    #print("Variance: " + str(var))
    #print("Skewness: " + str(skew))
    #print("Kurtosis: " + str(kurt))
    #print("Pc25: " + str(percentiles[0]))
    #print("Pc50: " + str(percentiles[1]))
    #print("Pc75: " + str(percentiles[2]))
    
    features = np.hstack((mean, median, std, var, skew, kurt, percentiles, silences, silence_mean, longest_silence, shortest_silence))

    return features

# Put it all on a numpy array
def get_features_numpy(info, local_max_up_bytes, local_min_up_bytes, local_max_up_packet, local_min_up_packet, 
                       local_max_down_bytes, local_min_down_bytes, local_max_down_packet, local_min_down_packet, zeros):
    np.set_printoptions(suppress=True)

    result = []

    print(info[0][1])
    
    for idx in range(0, len(info)):
        result.append(
            np.hstack(
                (
                 get_stats_numpy(info[idx][0]['up']['byte_count'], zeros[1]),
                 get_stats_numpy(info[idx][0]['up']['packet_count'], zeros[0]),
                 local_max_up_bytes[idx][0], local_min_up_bytes[idx][0],
                 local_max_up_packet[idx][0], local_min_up_packet[idx][0],
                 get_stats_numpy(info[idx][0]['down']['byte_count'], zeros[3]),
                 get_stats_numpy(info[idx][0]['down']['packet_count'], zeros[2]),
                 local_max_down_bytes[idx][0], local_min_down_bytes[idx][0],
                 local_max_down_packet[idx][0], local_min_down_packet[idx][0],
                 info[idx][1]
                )
            )
        )
    print(len(result[0]))
    return result

In [9]:
samples = get_features_numpy(info, local_max_up_bytes, local_min_up_bytes, local_max_up_packet, local_min_up_packet,
                                    local_max_down_bytes, local_min_down_bytes, local_max_down_packet, local_min_down_packet,
                                    zeros)
samples

netflix-openvpn


/home/agro/work/thesis/env/lib/python3.6/site-packages/numpy/core/fromnumeric.py:2957: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
/home/agro/work/thesis/env/lib/python3.6/site-packages/numpy/core/_methods.py:80: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)


137


[array(['-0.0674479703305377', '-0.16698178922631715',
        '0.1636665705119493', '0.026786746303142872', '1.3333433461954665',
        '0.1362105771682267', '-0.17679882739315209',
        '-0.16698178922631715', '-0.02118710327615268',
        '0.2501823870228692', '15.0', '1.5', '3.0', '1.0',
        '0.5638066065541967', '-0.28752257351460364', '1.4059590948743959',
        '1.9767209764600306', '1.458357028013498', '0.42761148406507443',
        '-0.3026038199559628', '-0.28752257351460364',
        '0.7177502249908512', '3.5160539575472702', '15.0', '1.5', '3.0',
        '1.0', '0.0784452858545705', '0.007752892703224287',
        '0.005006607656714788', '0.0020898292589174093',
        '0.0015777893569779862', '20.749432874416154', '10.60189314527793',
        '7.33603234563737', '4.0', '2.767819763927664',
        '0.018052175918307083', '0.006081101018941654',
        '0.004526169216996949', '0.0009866266221712336',
        '0.001488461713424155', '26.33208765046344', '12.3

Put it in a Pandas dataframe

In [10]:
names = [
            'up_bytes_mean', 'up_bytes_median', 'up_bytes_std', 'up_bytes_var', 'up_bytes_skew', 'up_bytes_kurt',
            'up_bytes_perc25', 'up_bytes_perc50', 'up_bytes_perc75', 'up_bytes_perc90',
            'up_bytes_silences', 'up_bytes_silence_mean', 'up_bytes_longest_silence', 'up_bytes_shortest_silence',
            'up_packet_mean', 'up_packet_median', 'up_packet_std', 'up_packet_var', 'up_packet_skew', 'up_packet_kurt',
            'up_packet_perc25', 'up_packet_perc50', 'up_packet_perc75', 'up_packet_perc90',
            'up_packet_silences', 'up_packet_silence_mean', 'up_packet_longest_silence', 'up_packet_shortest_silence',
            'up_bytes_1max_y', 'up_bytes_2max_y', 'up_bytes_3max_y', 'up_bytes_4max_y', 'up_bytes_5max_y',
            'up_bytes_1max_x', 'up_bytes_2max_x', 'up_bytes_3max_x', 'up_bytes_4max_x', 'up_bytes_5max_x',
            'up_bytes_1min_y', 'up_bytes_2min_y', 'up_bytes_3min_y', 'up_bytes_4min_y', 'up_bytes_5min_y',
            'up_bytes_1min_x', 'up_bytes_2min_x', 'up_bytes_3min_x', 'up_bytes_4min_x', 'up_bytes_5min_x',
            'up_packet_1max_y', 'up_packet_2max_y', 'up_packet_3max_y', 'up_packet_4max_y', 'up_packet_5max_y',
            'up_packet_1max_x', 'up_packet_2max_x', 'up_packet_3max_x', 'up_packet_4max_x', 'up_packet_5max_x',
            'up_packet_1min_y', 'up_packet_2min_y', 'up_packet_3min_y', 'up_packet_4min_y', 'up_packet_5min_y',
            'up_packet_1min_x', 'up_packet_2min_x', 'up_packet_3min_x', 'up_packet_4min_x', 'up_packet_5min_x',

            'down_bytes_mean', 'down_bytes_median', 'down_bytes_std', 'down_bytes_var', 'down_bytes_skew', 'down_bytes_kurt',
            'down_bytes_perc25', 'down_bytes_perc50', 'down_bytes_perc75', 'down_bytes_perc90',
            'down_bytes_silences', 'down_bytes_silence_mean', 'down_bytes_longest_silence', 'down_bytes_shortest_silence',
            'down_packet_mean', 'down_packet_median', 'down_packet_std', 'down_packet_var', 'down_packet_skew', 'down_packet_kurt',
            'down_packet_perc25', 'down_packet_perc50', 'down_packet_perc75', 'down_packet_perc90',
            'down_packet_silences', 'down_packet_silence_mean', 'down_packet_longest_silence', 'down_packet_shortest_silence',
            'down_bytes_1max_y', 'down_bytes_2max_y', 'down_bytes_3max_y', 'down_bytes_4max_y', 'down_bytes_5max_y',
            'down_bytes_1max_x', 'down_bytes_2max_x', 'down_bytes_3max_x', 'down_bytes_4max_x', 'down_bytes_5max_x',
            'down_bytes_1min_y', 'down_bytes_2min_y', 'down_bytes_3min_y', 'down_bytes_4min_y', 'down_bytes_5min_y',
            'down_bytes_1min_x', 'down_bytes_2min_x', 'down_bytes_3min_x', 'down_bytes_4min_x', 'down_bytes_5min_x',
            'down_packet_1max_y', 'down_packet_2max_y', 'down_packet_3max_y', 'down_packet_4max_y', 'down_packet_5max_y',
            'down_packet_1max_x', 'down_packet_2max_x', 'down_packet_3max_x', 'down_packet_4max_x', 'down_packet_5max_x',
            'down_packet_1min_y', 'down_packet_2min_y', 'down_packet_3min_y', 'down_packet_4min_y', 'down_packet_5min_y',
            'down_packet_1min_x', 'down_packet_2min_x', 'down_packet_3min_x', 'down_packet_4min_x', 'down_packet_5min_x',
            'label'
        ]
    
df = pd.DataFrame(samples, columns=names)

df

up_bytes_mean       up_bytes_median           up_bytes_std  \
0      -0.0674479703305377  -0.16698178922631715     0.1636665705119493   
1     -0.16290257072462325  -0.17618827579956953   0.022687588914038492   
2     -0.14927530946352557  -0.17601761148270512    0.06692198826793988   
3     -0.14577697540833257  -0.17553377814439441    0.06883302964400483   
4     -0.16385382518277286  -0.17675402800997517   0.022036212766472857   
5     -0.16382543801806773  -0.17668832224798237   0.022329865552378824   
6     -0.16316434134264046  -0.17693322554268284    0.02346606463446078   
7     -0.16392624374122897  -0.17668832224798237    0.02230948981437818   
8      -0.1641612769496041  -0.17693322554268284   0.022068628621829876   
9     -0.16351710448559928   -0.1767130685739277    0.02318988886157457   
10     -0.1690562993299629  -0.17693322554268284   0.017343310691872157   
11    -0.16296432276327535  -0.17585377373851524    0.02142668774952766   
12    -0.16322322053195873  -0.17676426786898702   0.023640445040027165   
13    -0.16445152006448488  -0.17639563294455984    0.02161896690328254   
14    -0.16326068134951044  -0.17666357592203702   0.024292096078235015   
15    -0.16325086815129072   -0.1761601161872869    0.02349763549717172   
16     -0.1628120901926323  -0.17676426786898702   0.023669686776721308   
17     -0.1726266821709255  -0.17668832224798237   0.010994187248415763   
18    -0.16303460801777073  -0.17675402800997517   0.024686178553191683   
19    -0.16323471192929428    -0.176843626776329   0.025258934639313724   
20    -0.16943565766229973  -0.17693322554268284    0.01542270268222876   
21    -0.17589783357631908  -0.17693322554268284   0.004152573521811652   
22    -0.17649541468181995  -0.17693322554268284   0.002512807535476571   
23    -0.17597468940701372  -0.17693322554268284  0.0031430785000292464   
24    -0.11276418194702525  -0.17675402800997517    0.14153603618600513   
25     -0.1594653913829734  -0.17458659118579675   0.026952126501879052   
26    -0.16507805721574711  -0.17676426786898702   0.021485091342907558   
27    -0.17311296169777793  -0.17673354829195143   0.013794356433381913   
28    -0.16260939787230294    -0.176843626776329   0.024006351665464824   
29    -0.16415937119806578    -0.176843626776329   0.022784054601166184   
...                    ...                   ...                    ...   
1038   -0.1643969074830883   -0.1626656886528154   0.007957009711202402   
1039  -0.16530370388669471  -0.16625987916598056   0.007705741109737775   
1040  -0.16489729526013486  -0.16646808963255516   0.009885359410583328   
1041   -0.1650140580969229  -0.16660120779970944    0.01055849887191598   
1042  -0.16365087686596821   -0.1625086774813001   0.010075873225829136   
1043  -0.16629833552538067   -0.1715197534117427   0.010223789580930136   
1044  -0.16329771550627006  -0.15835129472248224   0.010623708778717503   
1045  -0.16452263019651173   -0.1604777721106132   0.008802127894156565   
1046   -0.1630780420864127  -0.16350194380545113   0.009518265110783459   
1047  -0.16542351023713353  -0.16570692677933976   0.007810873895307273   
1048  -0.16347065534735933  -0.16249843762228822   0.007550653242785911   
1049  -0.16651997158488197  -0.16901781452650994   0.010386101451556764   
1050  -0.16532680045757697  -0.16729751821251637   0.011440589138247928   
1051   -0.1639053658064659  -0.16545775687671768   0.010623240175006087   
1052   -0.1661763674269282  -0.16666264695378064   0.008579052035365861   
1053  -0.16599250506955956  -0.16775489858171308     0.0079726361890757   
1054  -0.16840467452412167  -0.17173479045099188   0.007585354912155192   
1055  -0.16831877348463317  -0.17216827781582758    0.00794755195518118   
1056  -0.16740176566606774  -0.17054355351927808    0.00931882696473861   
1057   -0.1662743287448084  -0.16736919722559945   0.007928534944074722   
1058   -0.1670759959292263  -0.16889493621836757   0.007798147723895894   
1059  -0.16706894180412932  -0.1701203

Save it as .csv

In [11]:
outdir = 'csv/'
outname =  'all_60s_1s_32.csv'
if not os.path.exists(outdir):
    os.mkdir(outdir)
df.to_csv(os.path.join(outdir, outname), sep=',', encoding='utf-8')